In [1]:
#load_ext autotime
import pandas as pd
import geopandas as gpd
import geopy
from geopy.geocoders import Nominatim
from geopy.extra.rate_limiter import RateLimiter
import matplotlib.pyplot as plt
import plotly_express as px
import tqdm
from tqdm._tqdm_notebook import tqdm_notebook

<ipython-input-1-863b54eaad45>:10: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.*` instead of `tqdm._tqdm_notebook.*`
  from tqdm._tqdm_notebook import tqdm_notebook


In [2]:
locator = Nominatim(user_agent="measurements")

In [3]:
odf = pd.read_csv(r"T:\DCProjects\StoryMap\BikeCounting\BikeShare\Data\bike_share_locations.csv")
odf.head()

RouteID  BikeID   UserID                     Location           Latitude  \
0  14209422   19692  1949911            16th & Willamette  44.04216666666667   
1  14209423   20260  2045646         Matthew Knight Arena  44.04535833333333   
2  14209424   19770  2214468  Erb Memorial Union overflow  44.04526333333333   
3  14209425   19714  2214144            15th & University           44.04308   
4  14209426   19729  2028249            15th & University  44.04304333333334   

             Longitude        Date   Time OriginDestination  
0          -123.092915  2022-01-01  00:14            Origin  
1  -123.06533166666667  2022-01-01  00:20            Origin  
2  -123.07273333333333  2022-01-01  00:20            Origin  
3          -123.074745  2022-01-01  00:26            Origin  
4  -123.07477166666666  2022-01-01  00:27            Origin

In [4]:
'Knight Library (Virtual Hub)' in odf.Location.unique()

True

In [5]:
odf[odf.Latitude.isnull() | odf.Longitude.isnull()]

Empty DataFrame
Columns: [RouteID, BikeID, UserID, Location, Latitude, Longitude, Date, Time, OriginDestination]
Index: []

In [13]:
" - " in odf.Latitude.values

True

In [14]:
df = odf

In [15]:
df = df[df.Latitude != " - "]

In [16]:
" - " in df.Latitude.values

False

In [17]:
df["geom"] = df["Latitude"].map(str) + ',' + df['Longitude'].map(str)
df["geom"][0]

<ipython-input-17-5d67cbd21622>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["geom"] = df["Latitude"].map(str) + ',' + df['Longitude'].map(str)


'44.04216666666667,-123.092915'

In [18]:
locator = Nominatim(user_agent="measurements", timeout=10)
rgeocode = RateLimiter(locator.reverse, min_delay_seconds=0.00001)

In [19]:
tqdm_notebook.pandas()

In [20]:
df['address'] = df['geom'].progress_apply(rgeocode)
df.head()

  0%|          | 0/16790 [00:00<?, ?it/s]

<ipython-input-20-bc17bc9cec49>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['address'] = df['geom'].progress_apply(rgeocode)


RouteID  BikeID   UserID                     Location           Latitude  \
0  14209422   19692  1949911            16th & Willamette  44.04216666666667   
1  14209423   20260  2045646         Matthew Knight Arena  44.04535833333333   
2  14209424   19770  2214468  Erb Memorial Union overflow  44.04526333333333   
3  14209425   19714  2214144            15th & University           44.04308   
4  14209426   19729  2028249            15th & University  44.04304333333334   

             Longitude        Date   Time OriginDestination  \
0          -123.092915  2022-01-01  00:14            Origin   
1  -123.06533166666667  2022-01-01  00:20            Origin   
2  -123.07273333333333  2022-01-01  00:20            Origin   
3          -123.074745  2022-01-01  00:26            Origin   
4  -123.07477166666666  2022-01-01  00:27            Origin   

                                    geom  \
0          44.04216666666667,-123.092915   
1  44.04535833333333,-123.06533166666667   
2  44.04526333333333,-123.07273333333333   
3                   44.04308,-123.074745   
4  44.04304333333334,-123.07477166666666   

                                             address  
0  (2, West 16th Avenue, College Hill, Eugene, La...  
1  (Matthew Knight Arena, Franklin Boulevard, Eug...  
2  (University of Oregon, Sunset Alley, Eugene, L...  
3  (University of Oregon, Sunset Alley, Eugene, L...  
4  (University of Oregon, Sunset Alley, Eugene, L...

In [21]:
df.address[1]

Location(Matthew Knight Arena, Franklin Boulevard, Eugene, Lane County, Oregon, 97403-1221, United States, (44.0448264, -123.0663683756334, 0.0))

In [22]:
df.Location.isnull().values[3]

False

In [23]:
def getLoc(x):
    loc = x.raw['address']
    a = [key for key, value in loc.items()][0]
    b = [key for key, value in loc.items()][1]
    if  a == 'house_number':
        res = loc['road'] + ' ' + loc['house_number']
    else:
        res = loc[a]
        if res == "University of Oregon":
            res = "UO " + loc[b]
    return res

In [24]:
getLoc(df[df.Location.isnull().values].address.values[1])

'Villard Street 1544'

In [25]:
df['Name'] = df.address.apply(lambda x: getLoc(x))

<ipython-input-25-f89655196f91>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Name'] = df.address.apply(lambda x: getLoc(x))


In [26]:
sorted(df.Name.unique())

['13th & Olive',
 '13th and Olive (Willamate)',
 '16 Tons Café',
 '2125 Franklin',
 '3000s - Brooks Field',
 '4 Plus 3 Korean Barbaque',
 '5000s/6000s Brooks Field',
 '5th Street Public Market',
 '6th Street Alley',
 '7-Eleven',
 '76',
 '8000s - Brooks Field',
 '959 Franklin Apartments',
 'Actors Cabaret of Eugene',
 'Adams Street 356',
 'Adams Street 360',
 'Agate Street 1840',
 'Alder Street 1840',
 'Alder Street 2394',
 'Alder Street 2398',
 'Alder Street 950',
 "All Thai'd Up",
 'Allen Price Science Library',
 'Alpha Omega House',
 'Amazon Community Center',
 'Amazon Corners',
 'Amazon North/Jack Moore Field',
 'Amazon Parkway',
 'Amazon Parkway 2298',
 'Amazon Parkway 2456',
 'Amazon Parkway 2821',
 'Amazon Parkway 2841',
 'Amazon Path',
 'Amazon Pool',
 'Amazon Pool Facility',
 'Ambrosia Restaurant & Bar',
 'Andy',
 'Autzen Stadium',
 'Barnhart Hall',
 'Bates Steakhouse',
 'Bean West',
 'Berwick Hall',
 'Best Western Hayward Inn',
 'Beta Theta Pi',
 "Bill & Tim's Barbeque",
 'Bla

In [27]:
for n in df.loc[df.Location.isnull(),'Name'].unique():
    if all(df.loc[df['Name'] == n, 'Location'].isnull()):
        df.loc[df['Name'] == n, 'Location'] = n
    else:
        v = df.loc[df['Name'] == n, 'Location']
        df.loc[((df.Location.isnull()) & df['Name'] == n), 'Location'] = v[v.notnull()].values[0]    

C:\Users\clid1852\.conda\envs\geoenv\lib\site-packages\pandas\core\indexing.py:1720: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, value, pi)


In [28]:
df['Location'] = df['Location'].str.replace('University of Oregon','UO')

<ipython-input-28-daf40521dc37>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Location'] = df['Location'].str.replace('University of Oregon','UO')


In [29]:
def remove_street_number(x):
    x = str(x)
    if len(x.split(' ')[-2:-1]) == 0:
        res = x
    elif (x.split(' ')[-2:-1][0] in ['Avenue', 'Street', 'Alley']) and (x.split(' ')[-1:][0].isdigit()):
        res = x.rsplit(' ', 1)[0]
    else:
        res = x
    
    return res

In [30]:
df['Location'] = df['Location'].apply(lambda x: remove_street_number(x))

<ipython-input-30-090fb27860a0>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Location'] = df['Location'].apply(lambda x: remove_street_number(x))


In [31]:
df['Location'] = df['Location'].str.replace(' -',',')

<ipython-input-31-641b38609b57>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Location'] = df['Location'].str.replace(' -',',')


In [32]:
df.loc[df.Location == 'nan', 'Name']

30                                                     Rye
32                                                     Rye
33                                                     Rye
97                                            Kesey Square
98                                   Bill & Tim's Barbeque
                               ...                        
16661                                                  Rye
16671                                       Florence Apt's
16686                                            The Pearl
16762                                      UO Sunset Alley
16785    University of Oregon Library and Memorial Quad...
Name: Name, Length: 1029, dtype: object

In [33]:
df.loc[df.Location == 'nan', 'Location'] = df.loc[df.Location == 'nan', 'Name']

C:\Users\clid1852\.conda\envs\geoenv\lib\site-packages\pandas\core\indexing.py:1676: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(ilocs[0], value, pi)


In [34]:
for i in df.RouteID.unique():
    idx1 = ((df['RouteID'] == i) & (df['OriginDestination'] =='Origin'))
    idx2 = ((df['RouteID'] == i) & (df['OriginDestination'] =='Destination'))
    pathID = df.loc[idx1, 'Location'].values[0] + ' - ' + df.loc[idx2, 'Location'].values[0]
    df.loc[idx1, 'PathID'] = pathID
    df.loc[idx2, 'PathID'] = pathID

C:\Users\clid1852\.conda\envs\geoenv\lib\site-packages\pandas\core\indexing.py:1599: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[key] = infer_fill_value(value)
C:\Users\clid1852\.conda\envs\geoenv\lib\site-packages\pandas\core\indexing.py:1720: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, value, pi)
C:\Users\clid1852\.conda\envs\geoenv\lib\site-packages\pandas\core\indexing.py:1720: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a 

C:\Users\clid1852\.conda\envs\geoenv\lib\site-packages\pandas\core\indexing.py:1720: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, value, pi)
C:\Users\clid1852\.conda\envs\geoenv\lib\site-packages\pandas\core\indexing.py:1720: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, value, pi)
C:\Users\clid1852\.conda\envs\geoenv\lib\site-packages\pandas\core\indexing.py:1720: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice fro

C:\Users\clid1852\.conda\envs\geoenv\lib\site-packages\pandas\core\indexing.py:1720: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, value, pi)
C:\Users\clid1852\.conda\envs\geoenv\lib\site-packages\pandas\core\indexing.py:1720: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, value, pi)
C:\Users\clid1852\.conda\envs\geoenv\lib\site-packages\pandas\core\indexing.py:1720: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice fro

C:\Users\clid1852\.conda\envs\geoenv\lib\site-packages\pandas\core\indexing.py:1720: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, value, pi)
C:\Users\clid1852\.conda\envs\geoenv\lib\site-packages\pandas\core\indexing.py:1720: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, value, pi)
C:\Users\clid1852\.conda\envs\geoenv\lib\site-packages\pandas\core\indexing.py:1720: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice fro

C:\Users\clid1852\.conda\envs\geoenv\lib\site-packages\pandas\core\indexing.py:1720: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, value, pi)
C:\Users\clid1852\.conda\envs\geoenv\lib\site-packages\pandas\core\indexing.py:1720: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, value, pi)
C:\Users\clid1852\.conda\envs\geoenv\lib\site-packages\pandas\core\indexing.py:1720: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice fro

...

C:\Users\clid1852\.conda\envs\geoenv\lib\site-packages\pandas\core\indexing.py:1720: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, value, pi)
C:\Users\clid1852\.conda\envs\geoenv\lib\site-packages\pandas\core\indexing.py:1720: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, value, pi)
C:\Users\clid1852\.conda\envs\geoenv\lib\site-packages\pandas\core\indexing.py:1720: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice fro

C:\Users\clid1852\.conda\envs\geoenv\lib\site-packages\pandas\core\indexing.py:1720: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, value, pi)
C:\Users\clid1852\.conda\envs\geoenv\lib\site-packages\pandas\core\indexing.py:1720: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, value, pi)
C:\Users\clid1852\.conda\envs\geoenv\lib\site-packages\pandas\core\indexing.py:1720: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice fro

C:\Users\clid1852\.conda\envs\geoenv\lib\site-packages\pandas\core\indexing.py:1720: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, value, pi)
C:\Users\clid1852\.conda\envs\geoenv\lib\site-packages\pandas\core\indexing.py:1720: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, value, pi)
C:\Users\clid1852\.conda\envs\geoenv\lib\site-packages\pandas\core\indexing.py:1720: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice fro

C:\Users\clid1852\.conda\envs\geoenv\lib\site-packages\pandas\core\indexing.py:1720: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, value, pi)
C:\Users\clid1852\.conda\envs\geoenv\lib\site-packages\pandas\core\indexing.py:1720: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, value, pi)
C:\Users\clid1852\.conda\envs\geoenv\lib\site-packages\pandas\core\indexing.py:1720: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice fro

C:\Users\clid1852\.conda\envs\geoenv\lib\site-packages\pandas\core\indexing.py:1720: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, value, pi)
C:\Users\clid1852\.conda\envs\geoenv\lib\site-packages\pandas\core\indexing.py:1720: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, value, pi)
C:\Users\clid1852\.conda\envs\geoenv\lib\site-packages\pandas\core\indexing.py:1720: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice fro

In [35]:
df.tail()

RouteID  BikeID   UserID                          Location  \
16791  14224294   19620  2207368   PeaceHealth University District   
16792  14224297   19633  2211448                    17th & Hilyard   
16793  14224298   19811  2209431                     5th & Lincoln   
16794  14224302   19842  2028724  Eden's Bike Garage (Virtual Hub)   
16795  14224303   19635  1937401           17th & Pearl, East side   

                Latitude            Longitude        Date   Time  \
16791           44.04738  -123.08183833333334  2022-01-31  22:12   
16792  44.04108333333333  -123.08192333333334  2022-01-31  22:35   
16793          44.054305  -123.09692166666666  2022-01-31  22:46   
16794  44.05690666666667  -123.06536666666666  2022-01-31  23:23   
16795  44.04121333333333  -123.08951166666667  2022-01-31  23:59   

      OriginDestination                                   geom  \
16791       Destination           44.04738,-123.08183833333334   
16792       Destination  44.04108333333333,-123.08192333333334   
16793       Destination          44.054305,-123.09692166666666   
16794       Destination  44.05690666666667,-123.06536666666666   
16795       Destination  44.04121333333333,-123.08951166666667   

                                                 address  \
16791  (Peace Health Medical Center University Distri...   
16792  (Peace Lutheran, East 17th Avenue, College Hil...   
16793  (282, West 5th Avenue, Eugene, Lane County, Or...   
16794  (Papé Field, North Walnut Road, Eugene, Lane C...   
16795  (The Pearl, 1661, Pearl Street, College Hill, ...   

                                                  Name  \
16791  Peace Health Medical Center University District   
16792                                   Peace Lutheran   
16793                              West 5th Avenue 282   
16794                                       Papé Field   
16795                                        The Pearl   

                                                  PathID  
16791  Erb Memorial Union overflow - PeaceHealth Univ...  
16792           17th & Pearl, West side - 17th & Hilyard  
16793                     13th & Kincaid - 5th & Lincoln  
16794  Knight Law Center - Eden's Bike Garage (Virtua...  
16795  HEDCO Education Building - 17th & Pearl, East ...

In [36]:
ndf = df.drop(['geom', 'address'], axis=1)

In [37]:
ndf.tail()

RouteID  BikeID   UserID                          Location  \
16791  14224294   19620  2207368   PeaceHealth University District   
16792  14224297   19633  2211448                    17th & Hilyard   
16793  14224298   19811  2209431                     5th & Lincoln   
16794  14224302   19842  2028724  Eden's Bike Garage (Virtual Hub)   
16795  14224303   19635  1937401           17th & Pearl, East side   

                Latitude            Longitude        Date   Time  \
16791           44.04738  -123.08183833333334  2022-01-31  22:12   
16792  44.04108333333333  -123.08192333333334  2022-01-31  22:35   
16793          44.054305  -123.09692166666666  2022-01-31  22:46   
16794  44.05690666666667  -123.06536666666666  2022-01-31  23:23   
16795  44.04121333333333  -123.08951166666667  2022-01-31  23:59   

      OriginDestination                                             Name  \
16791       Destination  Peace Health Medical Center University District   
16792       Destination                                   Peace Lutheran   
16793       Destination                              West 5th Avenue 282   
16794       Destination                                       Papé Field   
16795       Destination                                        The Pearl   

                                                  PathID  
16791  Erb Memorial Union overflow - PeaceHealth Univ...  
16792           17th & Pearl, West side - 17th & Hilyard  
16793                     13th & Kincaid - 5th & Lincoln  
16794  Knight Law Center - Eden's Bike Garage (Virtua...  
16795  HEDCO Education Building - 17th & Pearl, East ...

In [38]:
ndf['Name'] = ndf['Name'].str.replace('University of Oregon','UO')
ndf['Name'] = ndf['Name'].str.replace('U of O','UO')

In [39]:
ndf.to_csv(r'T:\DCProjects\StoryMap\BikeCounting\BikeShare\Data\pathID.csv', index=False)